In [740]:
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import datetime
%matplotlib inline
#%load_ext tensorboard

print(tf.__version__)

2.6.0


In [741]:
class MandelbrotDataSet:
    def __init__(self, size=1000, max_depth=100, xmin=-2.0, xmax=0.7, ymin=-1.3, ymax=1.3):
        self.x = tf.random.uniform((size,),xmin,xmax,tf.float32)
        self.y = tf.random.uniform((size,),ymin,ymax,tf.float32)
        self.outputs = self.mandel(x=self.x, y=self.y,max_depth=max_depth)
        self.data = tf.stack([self.x, self.y], axis=1)

    @staticmethod
    def mandel(x, y, max_depth):
        zx, zy = x,y
        for n in range(1, max_depth):
            zx, zy = zx*zx - zy*zy + x, 2*zx*zy + y
        return tf.cast(tf.less(zx*zx+zy*zy, 4.0),tf.float32)

In [742]:
trainingData = MandelbrotDataSet(500_000)

In [743]:
#plt.scatter(trainingData.x, trainingData.y, s=1, c=trainingData.outputs)

In [744]:
model = tf.keras.Sequential([
    tf.keras.Input(shape=(2,)),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(100,activation="relu"),
    tf.keras.layers.Dense(1,activation=None)
])
model.compile(loss=tf.keras.losses.MeanSquaredError(), optimizer=tf.keras.optimizers.Adam(learning_rate=0.001),metrics=["mae"])
log_dir = "logs/fit/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir, histogram_freq=1)

history = model.fit(trainingData.data, trainingData.outputs,epochs=50,batch_size=100,callbacks=[tensorboard_callback])

2021-11-23 20:43:45.677326: I tensorflow/core/profiler/lib/profiler_session.cc:131] Profiler session initializing.
2021-11-23 20:43:45.677501: I tensorflow/core/profiler/lib/profiler_session.cc:146] Profiler session started.
2021-11-23 20:43:45.678946: I tensorflow/core/profiler/lib/profiler_session.cc:164] Profiler session tear down.


Epoch 1/50


2021-11-23 20:43:46.006081: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:112] Plugin optimizer for device_type GPU is enabled.


  18/5000 [..............................] - ETA: 50s - loss: 0.1782 - mae: 0.3029  

2021-11-23 20:43:46.278140: I tensorflow/core/profiler/lib/profiler_session.cc:131] Profiler session initializing.
2021-11-23 20:43:46.278150: I tensorflow/core/profiler/lib/profiler_session.cc:146] Profiler session started.
2021-11-23 20:43:46.308851: I tensorflow/core/profiler/lib/profiler_session.cc:66] Profiler session collecting data.
2021-11-23 20:43:46.312732: I tensorflow/core/profiler/lib/profiler_session.cc:164] Profiler session tear down.
2021-11-23 20:43:46.317136: I tensorflow/core/profiler/rpc/client/save_profile.cc:136] Creating directory: logs/fit/20211123-204345/train/plugins/profile/2021_11_23_20_43_46

2021-11-23 20:43:46.318005: I tensorflow/core/profiler/rpc/client/save_profile.cc:142] Dumped gzipped tool data for trace.json.gz to logs/fit/20211123-204345/train/plugins/profile/2021_11_23_20_43_46/MacBook-Air-de-ker.local.trace.json.gz
2021-11-23 20:43:46.322078: I tensorflow/core/profiler/rpc/client/save_profile.cc:136] Creating directory: logs/fit/20211123-204345/

5000/5000 [==============================] - 36s 7ms/step - loss: 0.0201 - mae: 0.0472

KeyboardInterrupt: 

In [ ]:
np.set_printoptions(precision=3, suppress=True)

hist = pd.DataFrame(history.history)
hist['epoch'] = history.epoch
hist.tail()
def plot_loss(history):
  plt.plot(history.history['loss'], label='loss')
#  plt.ylim([0, 10])
  plt.xlabel('Epoch')
  plt.ylabel('Error [mae]')
  plt.legend()
  plt.grid(True)

plot_loss(history)

In [ ]:
predictions = model.predict(trainingData.data)
print("predictions shape:", predictions.shape)

In [ ]:
plt.scatter(trainingData.x, trainingData.y, s=1, c=predictions)